# FUNCIÓN DE MODELO DE MACHINE LEARNING DE RECOMENDACIÓN DE PELICULAS 

In [1]:
import pandas as pd
from sklearn.neighbors import NearestNeighbors

In [2]:
#cargando los archivos de datos necesarios

datasets_final = pd.read_csv('/Users/benjaminzelaya/Desktop/ML_Proyecto_1/ETL - EDA/Analisis Exploratorio Datos/movies_data_final.csv')
data_genres = pd.read_csv('/Users/benjaminzelaya/Desktop/ML_Proyecto_1/ETL - EDA/Analisis Exploratorio Datos/genres_groupby.csv')
cast_idpel_df = pd.read_csv('/Users/benjaminzelaya/Desktop/ML_Proyecto_1/Proceso de Machine Learning/Cast_idPeliculas_df.csv')

In [3]:
datasets_final.head()

id original_language                                           overview  \
0    862                en  Led by Woody, Andy's toys live happily in his ...   
1   8844                en  When siblings Judy and Peter discover an encha...   
2  15602                en  A family wedding reignites the ancient feud be...   
3  31357                en  Cheated on, mistreated and stepped on, the wom...   
4  11862                en  Just when George Banks has recovered from his ...   

   popularity release_date  runtime    status  \
0   21.946943   1995-10-30     81.0  Released   
1   17.015539   1995-12-15    104.0  Released   
2   11.712900   1995-12-22    101.0  Released   
3    3.859495   1995-12-22    127.0  Released   
4    8.387519   1995-02-10    106.0  Released   

                                             tagline  \
0                                                NaN   
1          Roll the dice and unleash the excitement!   
2  Still Yelling. Still Fighting. Still Ready for...   
3  Friends are the people who let you be yourself...   
4  Just When His World Is Back To Normal... He's ...   

                         title  vote_average  ...  name_genres  id_genres  \
0                    Toy Story           7.7  ...    Animation       16.0   
1                      Jumanji           6.9  ...       Comedy       35.0   
2             Grumpier Old Men           6.5  ...       Family    10751.0   
3            Waiting to Exhale           6.1  ...    Adventure       12.0   
4  Father of the Bride Part II           5.7  ...      Fantasy       14.0   

              name_companies id_companies Cod_countries  \
0    Pixar Animation Studios          3.0            US   
1           TriStar Pictures        559.0            US   
2               Teitler Film       2550.0            US   
3  Interscope Communications      10201.0            US   
4               Warner Bros.       6194.0            US   

               country_name    budget      revenue  release_year     return  
0  United States of America  30000000  373554033.0          1995  12.451801  
1  United States of America  65000000  262797249.0          1995   4.043035  
2  United States of America         0          0.0          1995   0.000000  
3  United States of America  16000000   81452156.0          1995   5.090760  
4  United States of America         0   76578911.0          1995   0.000000  

[5 rows x 27 columns]

In [4]:
datasets_final.columns

Index(['id', 'original_language', 'overview', 'popularity', 'release_date',
       'runtime', 'status', 'tagline', 'title', 'vote_average', 'vote_count',
       'id_bellongs_to_collection', 'name_bellongs_to_collection',
       'poster_bellongs_to_collection', 'backdrop_bellongs_to_collection',
       'Cod_languages', 'name_languages', 'name_genres', 'id_genres',
       'name_companies', 'id_companies', 'Cod_countries', 'country_name',
       'budget', 'revenue', 'release_year', 'return'],
      dtype='object')

In [5]:
data_genres.head()

id                        name   id_genres
0     100            'Comedy' 'Crime'     '35,80'
1   10000            'Comedy' 'Drama'     '35,18'
2   10001  'Comedy' 'Science Fiction'    '35,878'
3  100010               'Drama' 'War'  '18,10752'
4  100017                     'Drama'        '18'

In [6]:
data_genres.rename(columns={'name': 'genero'},inplace=True)

## Crear Nuevo DataSets para prueba de ejercicio recomendacion de peliculas indicando nombre de pelicula utilizando popularity.

* El modelo de recomendación que se está utilizando en este caso se basa en el algoritmo de vecinos más cercanos (K-Nearest Neighbors o K-NN). Es un modelo de aprendizaje automático que se utiliza para encontrar objetos similares en función de las características de esos objetos.

* En el contexto de este sistema de recomendación de películas, el modelo de vecinos más cercanos busca películas similares a una película de consulta en términos de dos características: género y popularidad. Para ello, utiliza la métrica de distancia euclidiana para calcular la similitud entre las películas.


* Se cargan los datos de películas desde un data que concatenará un DataFrame de pandas complento y otro donde solamente usaremos dos columnas "title" y "popularity". Se realiza un preprocesamiento para manejar los valores faltantes (NaN) y transformar las columnas de género en variables ficticias (dummy variables).
crearemos  el modelo de vecinos más cercanos con un número determinado de vecinos y se ajusta a los datos de características.
Búsqueda de vecinos cercanos: Cuando se proporciona una película de consulta, el modelo encuentra las películas más cercanas a esa película en términos de género y popularidad.

* Las películas más similares encontradas son las recomendaciones que se devuelven como resultado, es decir, este modelo se basa en la idea de que si dos películas tienen características similares (en este caso, género y popularidad), es probable que los usuarios que disfruten de una película también disfruten de la otra. El algoritmo de vecinos más cercanos encuentra películas similares basándose en la distancia entre ellas en un espacio de características. Es importante tener en cuenta que este modelo de recomendación se enfoca en la similitud de las características y no en modelos de preferencias de usuarios o análisis de contenido más complejos.

In [7]:
# Agregar las nuevas columnas al dataset movie_genres
movie_ML = pd.concat([data_genres, datasets_final[['title', 'popularity']]], axis=1)

# Mostrar las primeras filas del dataset actualizado
movie_ML.head()

id                      genero   id_genres  \
0     100            'Comedy' 'Crime'     '35,80'   
1   10000            'Comedy' 'Drama'     '35,18'   
2   10001  'Comedy' 'Science Fiction'    '35,878'   
3  100010               'Drama' 'War'  '18,10752'   
4  100017                     'Drama'        '18'   

                         title  popularity  
0                    Toy Story   21.946943  
1                      Jumanji   17.015539  
2             Grumpier Old Men   11.712900  
3            Waiting to Exhale    3.859495  
4  Father of the Bride Part II    8.387519

In [8]:
# Ordenar la tabla según las columnas específicas
movie_ML = movie_ML
columns_order = ['id', 'title', 'genero', 'popularity']
movie_ML = movie_ML[columns_order]

# Redondear la columna "popularity" a dos decimales
movie_ML['popularity'] = movie_ML['popularity'].round(2)

# Eliminar caracteres no deseados de la columna "genero"
movie_ML['genero'] = movie_ML['genero'].str.replace(r'[\'"\s\[\]{}\\]', ' ', regex=True)
# Eliminar las comas de la columna "genero"
movie_ML['genero'] = movie_ML['genero'].str.replace(',', '')

In [9]:
movie_ML.head()

id                        title                      genero  popularity
0     100                    Toy Story             Comedy   Crime        21.95
1   10000                      Jumanji             Comedy   Drama        17.02
2   10001             Grumpier Old Men   Comedy   Science Fiction        11.71
3  100010            Waiting to Exhale                Drama   War         3.86
4  100017  Father of the Bride Part II                      Drama         8.39

In [10]:
# movie_data = movie_ML

# # Creo el dataframe con las columnas indicadas guardando el mismo dentro la carpeta de Machine Learning
# movie_data.to_csv("ML_data.csv", index=False)

In [60]:
# Quiero obtener la lista de pelis para tomar nombres y poner de ejemplo:

import pandas as pd


# Convertir los valores en la columna 'Actor' a cadenas de texto
movie_ML['title']= movie_ML['title'].astype(str)

# Obtener todos los nombres únicos en la columna 'title'
peliculas = movie_ML['title'].unique()

# Imprimir todos los nombres de actores uno por uno
for title in peliculas:
    print(title)

Toy Story
Jumanji
Grumpier Old Men
Waiting to Exhale
Father of the Bride Part II
Heat
Sabrina
Tom and Huck
Sudden Death
GoldenEye
The American President
Dracula: Dead and Loving It
Balto
Nixon
Cutthroat Island
Casino
Sense and Sensibility
Four Rooms
Ace Ventura: When Nature Calls
Money Train
Get Shorty
Copycat
Assassins
Powder
Leaving Las Vegas
Othello
Now and Then
Persuasion
The City of Lost Children
Shanghai Triad
Dangerous Minds
Twelve Monkeys
Wings of Courage
Babe
Carrington
Dead Man Walking
Across the Sea of Time
It Takes Two
Clueless
Cry, the Beloved Country
Richard III
Dead Presidents
Restoration
Mortal Kombat
To Die For
How To Make An American Quilt
Se7en
Pocahontas
When Night Is Falling
The Usual Suspects
Guardian Angel
Mighty Aphrodite
Lamerica
The Big Green
Georgia
Kids of the Round Table
Home for the Holidays
The Postman
The Confessional
The Indian in the Cupboard
Eye for an Eye
Mr. Holland's Opus
Don't Be a Menace to South Central While Drinking Your Juice in the Hood
Two 

In [57]:
# AQUI ARMO EL SISTEMA DE RECOMENDACION USANDO MODELO DE MACHINE LEARNING DE VECINOS MAS CERCANOS

import pandas as pd
from sklearn.neighbors import NearestNeighbors

def Pelis_recom(pelicula):
    # archivo CSV con los datos
    ML_DF1 = pd.read_csv('/Users/benjaminzelaya/Desktop/ML_Proyecto_1/Proceso de Machine Learning/ML_data.csv')

    # Buscar la película por título en la columna 'title'
    movie = ML_DF1[ML_DF1['title'] == pelicula]

    if len(movie) == 0:
        return "La película no se encuentra en la base de datos."

    # Obtener el género y la popularidad de la película
    movie_genero = movie['genero'].values[0]
    movie_popularity = movie['popularity'].values[0]

    # matriz de características para el modelo de vecinos más cercanos
    features = ML_DF1[['popularity']]
    genres = ML_DF1['genero'].str.get_dummies(sep=' ')
    features = pd.concat([features, genres], axis=1)

    # Manejar valores faltantes (NaN) reemplazándolos por ceros
    features = features.fillna(0)

    # modelo de vecinos más cercanos
    nn_model = NearestNeighbors(n_neighbors=6, metric='euclidean')
    nn_model.fit(features)

    # Encontrar las películas más similares (excluyendo la película de consulta indicada por usuario)
    _, indices = nn_model.kneighbors([[movie_popularity] + [0] * len(genres.columns)], n_neighbors=6)
    similar_movies_indices = indices[0][1:]  # Excluyendo la primera película que es la misma consulta
    Pelis_recom = ML_DF1.iloc[similar_movies_indices]['title']

    # Si la película de consulta está en la lista de recomendaciones, la eliminamos
    if pelicula in Pelis_recom.tolist():
        Pelis_recom = Pelis_recom[Pelis_recom != pelicula]

    return Pelis_recom



In [61]:
# Ejemplo de uso de la función

pelicula = 'Ace Ventura: When Nature Calls'
peliculas_recomendadas = Pelis_recom(pelicula)
print(f"Películas recomendadas para '{pelicula}':")
print(peliculas_recomendadas)


Películas recomendadas para 'Ace Ventura: When Nature Calls':
51046    Office Christmas Party
35913            Animals United
7248         The Quiet American
6164          The Shipping News
16676             The Objective
Name: title, dtype: object


/Library/Frameworks/Python.framework/Versions/3.10/lib/python3.10/site-packages/sklearn/base.py:464: UserWarning: X does not have valid feature names, but NearestNeighbors was fitted with feature names
  warnings.warn(


## PRUEBA DE SISTEMA DE RECOMENDACION DE PELICULAS POR NOMBRE DE ACTORES

In [12]:
# Quiero saber si estoy trabajando en la carpeta correcta

import os
print(os.getcwd())


/Users/benjaminzelaya/Desktop/ML_Proyecto_1/Proceso de Machine Learning


In [13]:
# Agregar las nuevas columnas al dataset movie_genres
movie_ML3= pd.concat([data_genres,cast_idpel_df, datasets_final[['title','popularity']]], axis=1)

pd.set_option('display.max_colwidth', None)

# Mostrar las primeras filas del dataset actualizado
movie_ML3.head(100)

id                      genero      id_genres  id_peliculas  \
0      100            'Comedy' 'Crime'        '35,80'           862   
1    10000            'Comedy' 'Drama'        '35,18'           862   
2    10001  'Comedy' 'Science Fiction'       '35,878'           862   
3   100010               'Drama' 'War'     '18,10752'           862   
4   100017                     'Drama'           '18'           862   
..     ...                         ...            ...           ...   
95   10050          'Comedy' 'Romance'     '35,10749'           949   
96   10051  'Comedy' 'Drama' 'Romance'  '35,18,10749'           949   
97   10052                     'Drama'           '18'           949   
98  100526     'Drama' 'Fantasy' 'War'  '18,14,10752'           949   
99  100528                     'Drama'           '18'           949   

                 Actor                        title  popularity  
0            Tom Hanks                    Toy Story   21.946943  
1            Tim Allen                      Jumanji   17.015539  
2          Don Rickles             Grumpier Old Men   11.712900  
3           Jim Varney            Waiting to Exhale    3.859495  
4        Wallace Shawn  Father of the Bride Part II    8.387519  
..                 ...                          ...         ...  
95     Hazelle Goodman               Les Miserables    1.479446  
96       Ray Buktenica                 Bed of Roses   10.412194  
97         Max Daniels                    Big Bully    2.936443  
98  Vince Deadrick Jr.                    Screamers   12.758848  
99         Steven Ford                    Screamers   12.758848  

[100 rows x 7 columns]

In [14]:
movie_ML3.drop('id', axis=1, inplace=True)
# dropeo la columna id creada que no tiene ninguna importancia 

In [15]:
movie_ML3.head(1000)

genero      id_genres  id_peliculas  \
0                  'Comedy' 'Crime'        '35,80'           862   
1                  'Comedy' 'Drama'        '35,18'           862   
2        'Comedy' 'Science Fiction'       '35,878'           862   
3                     'Drama' 'War'     '18,10752'           862   
4                           'Drama'           '18'           862   
..                              ...            ...           ...   
995    'Drama' 'Thriller' 'Mystery'   '18,53,9648'        117164   
996            'Animation' 'Comedy'        '16,35'        117164   
997     'Drama' 'History' 'Romance'  '18,36,10749'        117164   
998                'Action' 'Drama'        '28,18'        117164   
999  'Comedy' 'Foreign' 'Adventure'  '35,10769,12'        117164   

                  Actor                        title  popularity  
0             Tom Hanks                    Toy Story   21.946943  
1             Tim Allen                      Jumanji   17.015539  
2           Don Rickles             Grumpier Old Men   11.712900  
3            Jim Varney            Waiting to Exhale    3.859495  
4         Wallace Shawn  Father of the Bride Part II    8.387519  
..                  ...                          ...         ...  
995    Cynthia Rothrock  The Hunchback of Notre Dame   13.553999  
996  Marshall R. Teague                The Cable Guy    7.586577  
997      Daniel McVicar                      Kingpin   11.633347  
998        Lydie Denier                       Eraser    6.919314  
999        John O'Leary                       Eraser    6.919314  

[1000 rows x 6 columns]

In [16]:
# # armo un  primer data que contendra los valores para el sistema de recomendacion.
# movie_data_ML3= movie_ML3
# # Guardar el DataFrame en un archivo CSV llamado "ML_data3.csv"
# movie_data_ML3.to_csv("ML_data3.csv", index=False)

# print("El archivo ML_data3.csv ha sido creado exitosamente.")

In [17]:
# utilizando el data creado anteriormente sesgare mas columna para hacer un data mas pequeño para el sistema de recomendacion:

df_Machine_learning = pd.read_csv('/Users/benjaminzelaya/Desktop/ML_Proyecto_1/Proceso de Machine Learning/ML_data3.csv')

# Obtener las primeras 1000 filas del DataFrame
df_Machine_Learning = movie_ML3.head(1000)

# # Guardar las primeras 1000 filas en un nuevo archivo CSV
# df_Machine_learning.to_csv('DF_Machine_Learning.csv', index=False)


/var/folders/9h/wktndydj5rg6pj7yfx6ws1gm0000gn/T/ipykernel_28006/2999872090.py:3: DtypeWarning: Columns (0,1,4) have mixed types. Specify dtype option on import or set low_memory=False.
  df_Machine_learning = pd.read_csv('/Users/benjaminzelaya/Desktop/ML_Proyecto_1/Proceso de Machine Learning/ML_data3.csv')


# Prueba ML 3 - RECOMENDACION POR ACTORES

* LISTA DE ACTORES DEL DATA DE 1000 ACTORES, PARA ESTE EJERCICIO UTILIZO EL DATA LLAMADO DF_MACHINE_LEARNING.CSV

In [18]:
# Quiero obtener la lista de actores para tomar nombres y poner de ejemplo:

import pandas as pd


# Convertir los valores en la columna 'Actor' a cadenas de texto
df_Machine_learning['Actor'] = movie_ML3['Actor'].astype(str)

# Obtener todos los nombres únicos en la columna 'Actor'
actores_unicos = df_Machine_learning['Actor'].unique()

# Imprimir todos los nombres de actores uno por uno
for actor in actores_unicos:
    print(actor)


Tom Hanks
Tim Allen
Don Rickles
Jim Varney
Wallace Shawn
John Ratzenberger
Annie Potts
John Morris
Erik von Detten
Laurie Metcalf
R. Lee Ermey
Sarah Freeman
Penn Jillette
Robin Williams
Jonathan Hyde
Kirsten Dunst
Bradley Pierce
Bonnie Hunt
Bebe Neuwirth
David Alan Grier
Patricia Clarkson
Adam Hann-Byrd
Laura Bell Bundy
James Handy
Gillian Barber
Brandon Obray
Cyrus Thiedeke
Gary Joseph Thorup
Leonard Zola
Lloyd Berry
Malcolm Stewart
Annabel Kershaw
Darryl Henriques
Robyn Driscoll
Peter Bryant
Sarah Gilson
Florica Vlad
June Lion
Brenda Lockmuller
Walter Matthau
Jack Lemmon
Ann-Margret
Sophia Loren
Daryl Hannah
Burgess Meredith
Kevin Pollak
Whitney Houston
Angela Bassett
Loretta Devine
Lela Rochon
Gregory Hines
Dennis Haysbert
Michael Beach
Mykelti Williamson
Lamont Johnson
Wesley Snipes
Steve Martin
Diane Keaton
Martin Short
Kimberly Williams-Paisley
George Newbern
Kieran Culkin
BD Wong
Peter Michael Goetz
Kate McGregor-Stewart
Jane Adams
Eugene Levy
Lori Alan
Al Pacino
Robert De Niro


In [70]:
# AQUI ARMO EL SISTEMA DE RECOMENDACION USANDO MODELO DE MACHINE LEARNING DE VECINOS MAS CERCANOS

import pandas as pd
from sklearn.neighbors import NearestNeighbors
from sklearn.feature_extraction.text import TfidfVectorizer

def movie_recommendation_artista(Artista):
    movie_df = pd.read_csv('/Users/benjaminzelaya/Desktop/ML_Proyecto_1/Proceso de Machine Learning/DF_Machine_Learning.csv')

    # películas que tengan al actor especificado en la columna 'Actor'
    movies_with_artista = movie_df[movie_df['Actor'] == Artista]

    if len(movies_with_artista) == 0:
        return "La película no se encuentra en la base de datos."

    #  matriz de características para el modelo de vecinos más cercanos
    features = movie_df['genero'].str.get_dummies(sep=' ')

    # modelo de vecinos más cercanos solo con las características de género
    nn_model = NearestNeighbors(n_neighbors=6, metric='euclidean')
    nn_model.fit(features)

    # películas más similares (excluyendo las películas del actor indicado por usuario)
    indices = nn_model.kneighbors(features.iloc[movies_with_artista.index, :])

    # Recomendar películas similares
    movie_recommendation_artista = movie_df.iloc[indices[1][0][1:]]['title']

    return movie_recommendation_artista


In [72]:
# Ejemplo de uso de la función

artista = 'Robin Williams'
peliculas_recomendadas = movie_recommendation_artista(artista)
print(f"Películas recomendadas para '{artista}':")
print(peliculas_recomendadas)


/var/folders/9h/wktndydj5rg6pj7yfx6ws1gm0000gn/T/ipykernel_37471/2968427284.py:8: DtypeWarning: Columns (0,1,4) have mixed types. Specify dtype option on import or set low_memory=False.
  movie_df = pd.read_csv('/Users/benjaminzelaya/Desktop/ML_Proyecto_1/Proceso de Machine Learning/DF_Machine_Learning.csv')


Películas recomendadas para 'Robin Williams':
25862        Ginger & Rosa
26013             The Land
11962     The Book of Fate
44534           Blind Date
11235    Dead End Drive-In
Name: title, dtype: object


In [73]:

artista = 'Jim Varney'
peliculas_recomendadas = movie_recommendation_artista(artista)
print(f"Películas recomendadas para '{artista}':")
print(peliculas_recomendadas)

/var/folders/9h/wktndydj5rg6pj7yfx6ws1gm0000gn/T/ipykernel_37471/2968427284.py:8: DtypeWarning: Columns (0,1,4) have mixed types. Specify dtype option on import or set low_memory=False.
  movie_df = pd.read_csv('/Users/benjaminzelaya/Desktop/ML_Proyecto_1/Proceso de Machine Learning/DF_Machine_Learning.csv')


Películas recomendadas para 'Jim Varney':
14699                 10 Items or Less
44372    Las aventuras de Oliver Twist
40896          The Conquest of Everest
43278         Poppies Are Also Flowers
13118                           Asylum
Name: title, dtype: object


* Este modelo de Machine Learning se basa en el algoritmo de los vecinos más cercanos (K-Nearest Neighbors, K-NN) para recomendar películas basadas en los actores o actrices. El modelo busca similitudes entre las películas basándose en los actores o actrices que participaron en ellas. 

* Se empezo haciendo la carga del conjunto de datos que contiene información sobre las películas, en este caso utilice un dataframe llamada DF_Machine_Learning.csv, incluyendo los actores o actrices que participaron en ellas.
Para el Preprocesamiento de datos empece limpiando y transformar los datos. Que al principio me tiraba errores por los valores NaN, se manejan los valores faltantes (NaN) en la columna de actores o actrices y se utiliza la técnica TF-IDF (Term Frequency-Inverse Document Frequency) para convertir los nombres de los actores en características numéricas.


* Cuando se ingresa el nombre de un actor o actriz específico, el modelo busca las películas que contienen a ese actor o actriz en el conjunto de datos. Luego, utilizando el algoritmo de vecinos más cercanos, encuentra las películas más similares (excluyendo las películas del propio actor o actriz) y las recomienda como películas relacionadas que podrían ser de interés para el usuario.
Este modelo utiliza la distancia euclidiana en el espacio de características (nombres de actores transformados por TF-IDF) para medir la similitud entre películas. Las películas con actores o actrices similares tendrán una distancia euclidiana más pequeña y, por lo tanto, se consideran más cercanas en términos de similitud de actores o actrices.

* Tambien es posible que el modelo recomiende películas que tengan actores o actrices similares, pero no necesariamente significa que el usuario disfrutará todas las películas recomendadas, ya que siempre la eleccion depende del usuario. La efectividad de las recomendaciones dependerá siempre en gran medida de la calidad y cantidad de datos en el conjunto de datos, así como de la relevancia de los actores para las preferencias del usuario.